In [3]:
import tushare as ts
ts.set_token('78282dabb315ee578fb73a9b328f493026e97d5af709acb331b7b348')
pro = ts.pro_api()

ModuleNotFoundError: No module named 'tushare'

In [32]:
from datetime import datetime, timedelta
import pandas as pd
fees_df = pd.read_csv('./futures_fees_info.csv', usecols= [1, 4, 17, 19, 25],names=['合约', '合约乘数', '做多保证金率', '做空保证金率', '品种代码'])
data0 = int(fees_df[fees_df['合约'] == 'IH2407']['合约乘数'].iloc[0])

print(data0)
print(type(data0))
data1 = float(fees_df[fees_df['合约'] == 'IH2407']['做多保证金率'].iloc[0])
print(data1)
print(type(data1))
# fees_df[fees_df['合约'] == 'IH2407']['做空保证金率'].iloc[0]
# (fees_df[fees_df['合约'] == 'IH2407']['做多保证金率'].iloc[0] + fees_df[fees_df['合约'] == 'IH2407']['做空保证金率'].iloc[0])/2

300
<class 'int'>
0.15
<class 'float'>


In [10]:
from datetime import datetime, timedelta
import pandas as pd
fees_df = pd.read_csv('./futures_fees_info.csv', usecols= [1, 4, 17, 19],names=['合约', '合约乘数', '做多保证金率', '做空保证金率'])
contacts_df = pd.read_csv('./main_contacts.csv', usecols= [16, 17],names=['主连代码', '品种代码'])

def get_main_contact_on_time(main_symbol_code):
    data_str = ''
    alpha_chars = ''
    numeric_chars = ''
    main_code = ''

    # main_symbol = pro.fut_mapping(ts_code=main_symbol_code, trade_date = data_str).loc[0,'mapping_ts_code'].split('.')[0]
    # exchange_id = pro.fut_mapping(ts_code=main_symbol_code, trade_date = data_str).loc[0,'mapping_ts_code'].split('.')[1]
    main_symbol = contacts_df[contacts_df['品种代码'] == main_symbol_code]['主连代码'].iloc[0]


    # #   拆分主连合约代码为交易标识和交易所代码（交易市场）
    # main_symbol = pro.fut_mapping(ts_code=main_symbol_code, trade_date = data_str).loc[0,'mapping_ts_code'].split('.')[0]
    # exchange_id = pro.fut_mapping(ts_code=main_symbol_code, trade_date = data_str).loc[0,'mapping_ts_code'].split('.')[1]

    # #   拆分交易标识中的合约产品代码和交割月份
    # for char in main_symbol:
    #     if char.isalpha():
    #         alpha_chars += char
    #     elif char.isdigit():
    #         numeric_chars += char
    
    # #   监理交易所映射
    # exchange = {'CFX': 'CFFEX', 'SHF':'SHFE', 'DCE':'DCE', 'GFE':'GFEX', 'INE':'INE', 'ZCE':'CZCE'}

    # # 计算per_unit：交易单位(每手)和转换后交易所识别的main_code：主连代码
    # if exchange_id == 'CFX' or exchange_id == 'SHF' or exchange_id == 'DCE' or exchange_id == 'GFE' or exchange_id == 'INE':
    #     df = pro.fut_basic(exchange = exchange[exchange_id], fut_type='1', fut_code = alpha_chars, fields='ts_code,symbol,exchange,name,per_unit')
    #     # ts_code = df[df['symbol'] == main_symbol]['ts_code'].iloc[0]
    #     per_unit = df[df['symbol'] == main_symbol]['per_unit'].iloc[0]

    #     # ds = pro.fut_settle(trade_date = data_str, ts_code =ts_code)
    #     # ds['margin_rate'] = (ds['long_margin_rate'] + ds['short_margin_rate'])/2
    #     # margin_rate = ds['margin_rate'].iloc[0]
        
        
    #     if exchange_id == 'CFX':
    #         main_code = main_symbol
    #     elif exchange_id == 'SHF' or exchange_id == 'DCE' or exchange_id == 'GFE' or exchange_id == 'INE':
    #         lower_alpha_chars = str.lower(alpha_chars) 
    #         main_code = lower_alpha_chars + numeric_chars
    # elif exchange_id == 'ZCE':
    #     true_numeric_chars = numeric_chars[1:]
    #     main_code = alpha_chars + true_numeric_chars 
    #     df = pro.fut_basic(exchange = exchange[exchange_id], fut_type='1', fut_code = alpha_chars, fields='ts_code,symbol,exchange,name,per_unit')
    #     per_unit = df[df['symbol'] == main_code]['per_unit'].iloc[0]
    #     main_code = alpha_chars + true_numeric_chars

    # print("最终使用的主连代码：",main_code) 
    # print("%s的交易单位(每手):%s"%(main_symbol, per_unit))
    return main_symbol


In [11]:
get_main_contact_on_time('IH')

'IH2407'

In [ ]:
from datetime import datetime, timedelta
def get_main_contact_on_time(main_symbol_code):
    data_str = ''
    alpha_chars = ''
    numeric_chars = ''
    main_code = ''

    #   获取主连合约代码，如果是当天15点前日盘，则获取前一天的合约代码，如果是当天15点后晚盘，则获取今天的的合约代码
    now = datetime.now()
    if now.hour < 15:
        data_str = (now - timedelta(days=1)).date().strftime('%Y%m%d')
    else:
        data_str = now.date().strftime('%Y%m%d')

    #   拆分主连合约代码为交易标识和交易所代码（交易市场）
    main_symbol = pro.fut_mapping(ts_code=main_symbol_code, trade_date = data_str).loc[0,'mapping_ts_code'].split('.')[0]
    exchange_id = pro.fut_mapping(ts_code=main_symbol_code, trade_date = data_str).loc[0,'mapping_ts_code'].split('.')[1]

    #   拆分交易标识中的合约产品代码和交割月份
    for char in main_symbol:
        if char.isalpha():
            alpha_chars += char
        elif char.isdigit():
            numeric_chars += char
    
    #   监理交易所映射
    exchange = {'CFX': 'CFFEX', 'SHF':'SHFE', 'DCE':'DCE', 'GFE':'GFEX', 'INE':'INE', 'ZCE':'CZCE'}

    # 计算per_unit：交易单位(每手)和转换后交易所识别的main_code：主连代码
    if exchange_id == 'CFX' or exchange_id == 'SHF' or exchange_id == 'DCE' or exchange_id == 'GFE' or exchange_id == 'INE':
        df = pro.fut_basic(exchange = exchange[exchange_id], fut_type='1', fut_code = alpha_chars, fields='ts_code,symbol,exchange,name,per_unit')
        # ts_code = df[df['symbol'] == main_symbol]['ts_code'].iloc[0]
        per_unit = df[df['symbol'] == main_symbol]['per_unit'].iloc[0]

        # ds = pro.fut_settle(trade_date = data_str, ts_code =ts_code)
        # ds['margin_rate'] = (ds['long_margin_rate'] + ds['short_margin_rate'])/2
        # margin_rate = ds['margin_rate'].iloc[0]
        
        
        if exchange_id == 'CFX':
            main_code = main_symbol
        elif exchange_id == 'SHF' or exchange_id == 'DCE' or exchange_id == 'GFE' or exchange_id == 'INE':
            lower_alpha_chars = str.lower(alpha_chars) 
            main_code = lower_alpha_chars + numeric_chars
    elif exchange_id == 'ZCE':
        true_numeric_chars = numeric_chars[1:]
        main_code = alpha_chars + true_numeric_chars 
        df = pro.fut_basic(exchange = exchange[exchange_id], fut_type='1', fut_code = alpha_chars, fields='ts_code,symbol,exchange,name,per_unit')
        per_unit = df[df['symbol'] == main_code]['per_unit'].iloc[0]
        main_code = alpha_chars + true_numeric_chars

    print("最终使用的主连代码：",main_code) 
    print("%s的交易单位(每手):%s"%(main_symbol, per_unit))
    return main_code


In [ ]:
sb_1 = get_main_contact_on_time('IH.CFX')
sb_2 = get_main_contact_on_time('cu.SHF')
sb_3 = get_main_contact_on_time('eb.DCE')
sb_4 = get_main_contact_on_time('si.GFE')
sb_5 = get_main_contact_on_time('sc.INE') 
sb_6 = get_main_contact_on_time('SA.ZCE')

In [ ]:
# df = pro.fut_basic(exchange='DCE', fut_type='1',fut_code = 'j' , fields='ts_code,symbol,exchange,name,fut_code,multiplier,trade_unit,per_unit,quote_unit,quote_unit_desc,d_mode_desc,list_date,delist_date,d_month,last_ddate,trade_time_desc')
# df = pro.fut_basic(exchange='SHFE', fut_type='1', fut_code = 'au', fields='ts_code,symbol,name,list_date,delist_date')
df = pro.fut_basic(exchange='CZCE', fut_type='1', fut_code = 'SA', fields='ts_code,symbol,exchange,name,fut_code,per_unit')
# index_of_value = df.index[df['symbol'] == 'AU2408']
df.head()
value = df[df['symbol'] == 'SA409']['per_unit'].iloc[0]
print(value)
# df.loc[index_of_value, 'per_unit'].value
# df.head()

In [ ]:
df = pro.fut_mapping(ts_code='SA.ZCE')
print(df)

In [ ]:
# ds = pro.fut_settle(trade_date = '20240625', ts_code ='SA2409.ZCE')
# ds = pro.fut_settle(trade_date='20230625', exchange='ZCE')
# ds = pro.fut_settle(ts_code='SA409.ZCE', exchange='CZCE')
# pro.fut_settle(trade_date='20181114', exchange='CZCE')
pro.fut_settle(ts_code='AP2510.ZCE', exchange='CZCE')

In [ ]:
ds.head()

In [ ]:
ds['margin_rate'] = round((ds['long_margin_rate'] + ds['short_margin_rate'])/2,2)

In [ ]:
ds['margin_rate'].iloc[0]

In [ ]:
value = df.loc[index_of_value, 'per_unit'].iloc[0]

In [ ]:
print(value)

In [ ]:
df_IH = pro.fut_mapping(ts_code='IH.CFX')
print(df_IH)
df_IH.to_csv(r"E:\data\mapping_ts_code_IH.csv")

In [ ]:
df_IF = pro.fut_mapping(ts_code='IF.CFX')
print(df_IF)
df_IF.to_csv(r"E:\data\mapping_ts_code_IF.csv")

In [ ]:
df_IC = pro.fut_mapping(ts_code='IC.CFX')
print(df_IC)
df_IC.to_csv(r"E:\data\mapping_ts_code_IC.csv")

In [ ]:
df_IM = pro.fut_mapping(ts_code='IM.CFX')
print(df_IM)
df_IM.to_csv(r"E:\data\mapping_ts_code_IM.csv")

In [ ]:
df_TF = pro.fut_mapping(ts_code='TF.CFX')
print(df_TF)
df_TF.to_csv(r"E:\data\mapping_ts_code_TF.csv")

In [ ]:
df_T = pro.fut_mapping(ts_code='T.CFX')
print(df_T)
df_T.to_csv(r"E:\data\mapping_ts_code_T.csv")

In [ ]:
df_TS = pro.fut_mapping(ts_code='TS.CFX')
print(df_TS)
df_TS.to_csv(r"E:\data\mapping_ts_code_TS.csv")

In [ ]:
df_TL = pro.fut_mapping(TL_code='TL.CFX')
print(df_TL)
df_TL.to_csv(r"E:\data\mapping_TL_code_TL.csv")

In [1]:
df_TL = pro.fut_mapping(ts_code='TL.CFX')
print(df_TL)
df_TL.to_csv(r"D:\data\mapping_TL_code_TL.csv")

NameError: name 'pro' is not defined

In [ ]:
import akshare as ak

futures_comm_info_df = ak.futures_comm_info(symbol="上海国际能源交易中心")
print(futures_comm_info_df["保证金-买开"])

In [ ]:
futures_fees_info_df = ak.futures_fees_info()
print(futures_fees_info_df)

In [ ]:
futures_fees_info_df.to_csv(r'./futures_fees_info.csv', index=False)

In [ ]:
futures_display_main_sina_df = ak.futures_display_main_sina()
print(futures_display_main_sina_df)

In [ ]:
import pandas as pd
url = 'https://www.9qihuo.com/hangqing' #上期所铜结算参数地址https://www.9qihuo.com/hangqing
data =pd.read_html(url) #读取网页上的表格
dt=data[4].drop([0],axis=0).append(data[5],ignore_index=True) #提取结算参数到DataFrame格式
#调整格式
dt.columns=dt.iloc[0]
dt.drop([0],axis=0,inplace=True) 
dt.set_index('合约代码',inplace=True)
print(dt) #输出铜的结算参数

In [ ]:
import requests
from bs4 import BeautifulSoup
import csv

# 目标网址
url = "https://www.9qihuo.com/hangqing"

# 发送GET请求，禁用SSL验证
response = requests.get(url, verify=False)
response.encoding = 'utf-8'  # 确保编码正确

# 解析网页内容
soup = BeautifulSoup(response.text, 'lxml')

# 找到目标表格
table = soup.find('table', {'id': 'tblhangqinglist'})

# 初始化CSV文件
with open('main_contacts.csv', mode='w', newline='', encoding='utf-8') as file:
    writer = csv.writer(file)
    
    # 遍历表格的所有行
    for row in table.find_all('tr'):
        # 获取每一行的所有单元格
        cols = row.find_all(['th', 'td'])
        # 提取文本内容并写入CSV文件
        writer.writerow([col.text.strip() for col in cols])

print("表格已成功保存为main_contacts.csv")




In [ ]:
import pandas as pd
df = pd.read_csv('./main_contacts.csv')
df.head()

In [ ]:
df['交易品种'] = df['合约'].str.split(r'[()]', n=1, expand=True)[0]
df['主连代码'] = df['合约'].str.split(r'[()]', n=2, expand=True)[1]

# df['品种代码'] = df['主连代码'].str.split(str.isalpha(df['主连代码']), n=1, expand=True)[0]

In [ ]:
import pandas as pd
import re

# 创建示例DataFrame

# 定义拆分字母和数字的函数
def split_alpha_numeric(s):
    match = re.match(r"([a-zA-Z]+)([0-9]+)", s)
    if match:
        return match.groups()
    else:
        return (s, None)  # 如果没有匹配，返回原始字符串和None

# 应用函数并创建新列
df[['品种代码', '交割月份']] = df['主连代码'].apply(lambda x: pd.Series(split_alpha_numeric(x)))

print(df)


In [ ]:
df.to_csv('./main_contacts_all.csv')

In [39]:
import subprocess
import schedule
import time
from datetime import datetime

#   jerome：增加akshare库
import akshare as ak

#   jerome:增加下列库用于爬虫获取主力连续代码
import pandas as pd
import requests
from bs4 import BeautifulSoup
import csv
import re
import os

In [48]:
def get_futures_fees_info():
    futures_fees_info_df = ak.futures_fees_info()
    futures_fees_info_df.to_csv(r'./futures_fees_info.csv', index=False)

def get_main_contacts():
    url = "https://www.9qihuo.com/hangqing"

    # 发送GET请求，禁用SSL验证
    response = requests.get(url, verify=False)
    response.encoding = 'utf-8'  # 确保编码正确

    # 解析网页内容
    soup = BeautifulSoup(response.text, 'lxml')

    # 找到目标表格
    table = soup.find('table', {'id': 'tblhangqinglist'})

    # 初始化CSV文件
    with open('tmp_main_contacts.csv', mode='w', newline='', encoding='utf-8') as file:
        writer = csv.writer(file)
        
        # 遍历表格的所有行
        for row in table.find_all('tr'):
            # 获取每一行的所有单元格
            cols = row.find_all(['th', 'td'])
            # 提取文本内容并写入CSV文件
            writer.writerow([col.text.strip() for col in cols])

    df = pd.read_csv('./tmp_main_contacts.csv',encoding='utf-8')
    df['交易品种'] = df['合约'].str.split(r'[()]', n=1, expand=True)[0]
    df['主连代码'] = df['合约'].str.split(r'[()]', n=2, expand=True)[1]

    df[['品种代码', '交割月份']] = df['主连代码'].apply(lambda x: pd.Series(split_alpha_numeric(x)))
    df.to_csv('./main_contacts.csv')

    print("期货主力品种表已经保存为main_contacts.csv")
    os.remove("./tmp_main_contacts.csv")

#   拆分字母和数字的函数
def split_alpha_numeric(s):
    match = re.match(r"([a-zA-Z]+)([0-9]+)", s)
    if match:
        return match.groups()
    else:
        return (s, None)  # 如果没有匹配，返回原始字符串和None

In [44]:
get_futures_fees_info()

In [49]:
get_main_contacts()

期货主力品种表已经保存为main_contacts.csv
